## Day 22: Monkey Map

### Part 1

[![nbviewer](https://raw.githubusercontent.com/jupyter/design/master/logos/Badges/nbviewer_badge.svg)](https://nbviewer.org/github/mazharenko/AoC-2022/tree/HEAD/notebooks/day22/puzzle1.ipynb)

#### Parsing

In [134]:
#!value --name sampleRaw --from-file ./data_sample.txt

In [135]:
#!share sampleRaw --from value
sampleRaw

        ...#
        .#..
        #...
        ....
...#.......#
........#...
..#....#....
..........#.
        ...#....
        .....#..
        .#......
        ......#.

10R5L5R10L4R5L5

In [136]:
#load "../common/common.fsx"

open System.Text.RegularExpressions

type Instruction = | Clockwise | Counterclockwise | Forward of int
type Instructions = Instruction list
type Tile = | Open | Wall | Empty
type Tiles = Tile[,]

let parse s : Tiles * Instructions = 
    let [|mapString; pathString|] = Pattern2.read id s
    let mapRows = Pattern1.read id mapString
    let rows = Array.length mapRows
    let cols = mapRows |> Array.map String.length |> Array.max
    let map = Array2D.init rows cols (fun i j -> 
        if j < String.length mapRows[i] 
        then 
            match mapRows[i][j] with
            | '.' -> Open
            | '#' -> Wall
            | _ -> Empty
        else Empty
    )
    let regex = Regex "(\d+)|\D"
    let path = 
        regex.Matches (pathString.Trim())
        |> Seq.map (fun x -> x.Value)
        |> Seq.map (function | "L" -> Counterclockwise | "R" -> Clockwise | x -> x |> int |> Forward)
        |> Seq.toList
    map, path


In [137]:
#load "../common/matrixFormatting.fsx"

let displayMap (map : Tiles) = 
    let color = 
        function 
        | Open -> System.Drawing.Color.Gray
        | Wall -> System.Drawing.Color.Blue
        | Empty -> System.Drawing.Color.Transparent
    toDisplayable color map

In [138]:
let sampleMap, sampleInstructions = parse sampleRaw
sampleMap |> displayMap |> display
sampleInstructions |> display

index type Item 0 FSI_0227+Instruction+Forward 10 1 FSI_0227+Instruction+_Clockwise 2 FSI_0227+Instruction+Forward 5 3 FSI_0227+Instruction+_Counterclockwise 4 FSI_0227+Instruction+Forward 5 5 FSI_0227+Instruction+_Clockwise 6 FSI_0227+Instruction+Forward 10 7 FSI_0227+Instruction+_Counterclockwise 8 FSI_0227+Instruction+Forward 4 9 FSI_0227+Instruction+_Clockwise 10 FSI_0227+Instruction+Forward 5 11 FSI_0227+Instruction+_Counterclockwise 12 FSI_0227+Instruction+Forward 5

The actual input:

In [139]:
#!value --name actualRaw --from-file ./data_actual.txt

In [140]:
#!share actualRaw --from value
let actualMap, actualInstructions = parse actualRaw
actualMap |> displayMap |> withSettings { Width = 600 } |> display
actualInstructions |> display

index type Item 0 FSI_0227+Instruction+Forward 23 1 FSI_0227+Instruction+_Counterclockwise 2 FSI_0227+Instruction+Forward 34 3 FSI_0227+Instruction+_Clockwise 4 FSI_0227+Instruction+Forward 4 5 FSI_0227+Instruction+_Counterclockwise 6 FSI_0227+Instruction+Forward 9 7 FSI_0227+Instruction+_Clockwise 8 FSI_0227+Instruction+Forward 5 9 FSI_0227+Instruction+_Counterclockwise 10 FSI_0227+Instruction+Forward 23 11 FSI_0227+Instruction+_Clockwise 12 FSI_0227+Instruction+Forward 42 13 FSI_0227+Instruction+_Counterclockwise 14 FSI_0227+Instruction+Forward 32 15 FSI_0227+Instruction+_Counterclockwise 16 FSI_0227+Instruction+Forward 17 17 FSI_0227+Instruction+_Counterclockwise 18 FSI_0227+Instruction+Forward 25 19 FSI_0227+Instruction+_Clockwise ... (more)

#### Solution

When dealing with facing, it is convenient to represent it as a unit vector. 

In [141]:
type Facing = Point

let down : Facing = Point (1,0)
let up : Facing = Point (-1,0)
let right : Facing = Point (0,1)
let left : Facing = Point (0,-1)

For facing transformations, this notebook relies on the vector rotation implementation from the `rotation.fsx` file, which contains implementations for clockwise and counterclockwise rotation and a function to apply them to a vector.

In [142]:
#load "./rotation.fsx"

down |> display
down
|> Rotation2.rotate Rotation2.cw

Item ( 1, 0 )

Item ( 0, -1 )

Rotations are composable.

In [143]:
down
|> Rotation2.rotate (Rotation2.cw * Rotation2.cw * Rotation2.cw)

Item ( 0, 1 )

The `findCoord` function below finds new coordinates respecting the structure of the map. It calls itself recursively with an increased `diff` value if the target tile is `Empty`. It is expected that it is initially called with a unit `diff` vector.

In [144]:
let rec findCoord (map : Tile[,]) (from: Point) (diff: Point) : Point =
    let (Point(newx,newy)) = from + diff
    let newxNormalized = newx %% (Array2D.length1 map)
    let newyNormalized = newy %% (Array2D.length2 map)
    match map[newxNormalized, newyNormalized] with
    | Open -> Point(newxNormalized, newyNormalized)
    | Wall -> from
    | Empty -> findCoord map from (diff + Point.dir diff)
        

When executing a `Forward` instruction, `findCoord` must be called several times according to the steps number. Here, all intermediate point are preserved for visualization purporses.

In [145]:
type Position = {Coordinates: Point; Facing: Facing}
type PathItem = { Position: Position; IntermediatePositions: Position list }

let rec private move' map position instructions =
    match instructions with
    | [] -> []
    | instruction::rest ->
        let pathItem = 
            match instruction, position with
            | Clockwise, _ -> 
                {
                    Position = { position with Facing = Rotation2.rotate Rotation2.cw position.Facing }
                    IntermediatePositions = []
                }
            | Counterclockwise, _ -> 
                {
                    Position = { position with Facing = Rotation2.rotate Rotation2.ccw position.Facing }
                    IntermediatePositions = []
                }
            | Forward steps, pos ->
                let newCoordinates = 
                    List.unfold (
                        fun (c,stepsLeft) -> 
                            if stepsLeft <= 0 then None
                            else 
                                let newp = findCoord map c pos.Facing
                                if (newp = c) then None
                                else Some (newp, (newp, stepsLeft - 1))
                    ) (pos.Coordinates, steps)
                    |> List.rev
                match newCoordinates with
                | [] -> 
                    {
                        Position = {position with Coordinates = pos.Coordinates}
                        IntermediatePositions = []
                    }
                | coordinates ->     
                    {
                        Position = {position with Coordinates = newCoordinates |> List.head}
                        IntermediatePositions = 
                            newCoordinates 
                            |> List.tail
                            |> List.map (fun p -> {position with Coordinates = p})
                    }
        move' map (pathItem.Position) rest @ [pathItem]

let move map position instructions =
    move' map position instructions @ [{Position = position; IntermediatePositions=[]}]

                   

In [146]:

let private start = Point(0, (sampleMap[0,*] |> Array.findIndex ((=)Open)))
let private pos =  {Facing = right; Coordinates = start}
let samplePath = move sampleMap pos sampleInstructions

To visualize the maps with the paths we might want to draw smaller "pixels" for the steps. Without changing our helpers, this can be done by replicating the map matrices, thus increasing the "pixel" density.

In [147]:
let withPathDisplayable (map : Tile[,]) (path : PathItem list) =
    let newMap = Array2D.init (3 * Array2D.length1 map) (3 * Array2D.length2 map) (fun i j -> map[i/3, j/3])
    
    let pathMap = Array2D.create (Array2D.length1 newMap) (Array2D.length2 newMap) System.Drawing.Color.Empty
    path
    |> Seq.collect (fun pi -> 
        [
            yield (Point.x pi.Position.Coordinates)*3+1, (Point.y pi.Position.Coordinates)*3+1
            yield! 
                pi.IntermediatePositions
                |> List.collect (fun p -> 
                    let (Point(x,y)) = p.Coordinates
                    match p.Facing with
                    | f when f = down || f = up ->
                        [ x*3,y*3+1; x*3+1,y*3+1; x*3+2,y*3+1 ]
                    | f when f = left || f = right ->
                        [ x*3+1,y*3; x*3+1,y*3+1; x*3+1,y*3+2 ]
                )
        ]
    )
    |> Seq.iter (fun (i,j) -> 
        pathMap[i,j] <- System.Drawing.Color.Black
    )

    let (Point(endX, endY)) = (List.head path).Position.Coordinates
    List.allPairs [0;1;-1] [0;1;-1]
    |> List.iter (fun (dx,dy) -> 
        pathMap[endX*3+dx+1, endY*3+dy+1] <- System.Drawing.Color.Red
    )
    
    newMap 
    |> displayMap
    |> withMatrix pathMap id


withPathDisplayable sampleMap samplePath |> display

In [148]:
let password (pi : PathItem) = 
    let facing =
        match pi.Position.Facing with
        | x when x = down -> 1
        | x when x = left -> 2
        | x when x = up -> 3
        | x when x = right -> 0
        | _ -> failwith ""
    let (Point(x, y)) = pi.Position.Coordinates
    1000 * (x+1) + 4 * (y+1) + facing

In [149]:
samplePath |> List.head |> password

6032

In [150]:
let private start = Point(0, (actualMap[0,*] |> Array.findIndex ((=)Open)))
let private pos =  {Facing = right; Coordinates = start}
let actualPath = move actualMap pos actualInstructions

In [151]:
withPathDisplayable actualMap actualPath |> withSettings {Width = 900} |> display